In [24]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import utils
import metrics

import os

from scipy.ndimage import gaussian_filter1d

#import burst_detector as bd

%matplotlib inline
%config InlineBackend.figure_format = 'retina'

In [16]:
# parameters for animal
file_dir = "Z:/Wu_sleep/m1/SD1/"
file_date = "20240914"
t_stamp = ["0900", "1000", "1100", "1200", "1300", "1400", "1500", "1600", "1700", "1800", "1900", "2000", "2100"]

# parameters for math
bin_size = 30000
sample_rate = 30000
sigma = 6

burst_freq = 100

In [3]:
# loop over sessions for one animal

spikes = []
for s in range(len(t_stamp)):

    file_path = file_date + "_SD1_test_" + t_stamp[s] + "_g0/catgt_" + file_date + "_SD1_test_" + t_stamp[s] + "_g0/" + file_date + "_SD1_test_" + t_stamp[s] + "_g0_imec0/imec0_ks25"
    spike_times_file = file_dir + file_path + "/spike_times.npy"
    spike_clusters_file = file_dir + file_path + "/spike_clusters.npy"
    cluster_group_file = file_dir + file_path + "/cluster_group.tsv"

    # spike times by cluster
    spike_times, spike_clusters, clust_labels = utils.load_files(spike_times_file, spike_clusters_file, cluster_group_file)
    spike_times_all = utils.spike_times_by_cluster(spike_times, spike_clusters, clust_labels)
    spikes.append(spike_times_all)

    # update metrics file and save as metrics_curated
    fr_df = metrics.firing_rate_metics(spike_times, spike_clusters, clust_labels)
    burst_count, burst_ratio = metrics.bursting_metrics(spike_times_all, burst_freq, sample_rate)

    fr_df["burst_count"] = burst_count
    fr_df["burst_ratio"] = burst_ratio

    fr_df.to_csv(os.path.join(file_dir + file_path, r"metrics_curated.csv"), mode='w+')

In [ ]:
spike_times_file = r"Z:\Wu_sleep\m2\SD1\20240923_SD1_test_0900_g0\catgt_20240923_SD1_test_0900_g0\20240923_SD1_test_0900_g0_imec0\imec0_ks25\spike_times.npy"
spike_clusters_file =r"Z:\Wu_sleep\m2\SD1\20240923_SD1_test_0900_g0\catgt_20240923_SD1_test_0900_g0\20240923_SD1_test_0900_g0_imec0\imec0_ks25\spike_clusters.npy"
cluster_group_file = r"Z:\Wu_sleep\m2\SD1\20240923_SD1_test_0900_g0\catgt_20240923_SD1_test_0900_g0\20240923_SD1_test_0900_g0_imec0\imec0_ks25\cluster_group.tsv"

spike_times, spike_clusters, clust_label = utils.load_files(spike_times_file, spike_clusters_file, cluster_group_file)
spikes = utils.spike_times_by_cluster(spike_times, spike_clusters, clust_label)

fr_df = metrics.firing_rate_metics(spike_times, spike_clusters, clust_label)

In [ ]:
fr_df

In [ ]:
for i in range(len(spike_times_all)):
    if len(spike_times_all[i]) == 0:
        print(i)

In [ ]:
len(spikes[0][23])

In [ ]:
q_all = []
burst_thres = 20

spike_t_delta = []

for i in range(len(spikes)):
    clust_t_delta = np.diff(spikes[i])
    spike_t_delta.append(sum(clust_t_delta <= (0.05*sample_rate)))

In [ ]:
plt.plot(q_all)
plt.plot(spike_t_delta)
plt.show()

In [ ]:
aa = [1,2,3,4,5,6,7,8,9,10]
bb = [2,4,6,3,5,3,5,7,3,2]
cc = [1,2,5,2,4,6,2,3,5,5]

gg = pd.DataFrame({"cluster_id":aa, "bb":bb})

In [ ]:
gg["cc"] = cc

print(gg)

In [ ]:
# code logic for burst detection based on ISI

pp = [0, 1, 0, 0 ,0 ,1, 0,0,1 ,0,0,1]

b = [(pp[i]^pp[i+1]) for i in range(len(pp)-1)]

print(b)

[1, 1, 0, 0, 1, 1, 0, 1, 1, 0, 1]


In [59]:
import math
animal_folder = r"C:\Users\alexc\Desktop\Neuron_Tracking\Mark_Sleep\M4"
session_folder = ["\D1", "\D2", "\D3", "\D4", "\D5", "\D6", "\D7", "\D8", "\D9", "\D10", "\D11", "\D12", "\D13"]
#session_folder = ["\D1", "\D2", "\D3", "\D4", "\D5", "\D6", "\D7", "\D8"]

#folder = "\D1"

for f in session_folder:
    folder = f
    spike_times_file = animal_folder + folder + "\spike_times.npy"
    spike_clusters_file = animal_folder + folder + "\spike_clusters.npy"
    cluster_group_file = animal_folder + folder + "\cluster_group.tsv"
    metrics_file = animal_folder + folder + "\metrics.tsv"

    spike_times, spike_clusters, clust_label = utils.load_files(spike_times_file, spike_clusters_file, cluster_group_file)
    spikes = utils.spike_times_by_cluster(spike_times, spike_clusters, clust_label)
    rec_len = np.max(spike_times)/sample_rate

    burst_count = []
    for c in range(len(spikes)):
        spike_delta = np.diff(spikes[c])
        spike_ISI = spike_delta < (0.05*sample_rate)

        burst_edge = [(spike_ISI[i]^spike_ISI[i+1]) for i in range(len(spike_ISI)-1)]
        burst_count.append(math.floor(sum(burst_edge)/2))

    met_file = pd.read_csv(metrics_file, sep='\t')
    met_file["burst_count"] = np.zeros(len(met_file["cluster_id"]))
    met_file["burst_freq"] = np.zeros(len(met_file["cluster_id"]))

    for i in range(len(clust_label)):
        ind = met_file.index[met_file["cluster_id"] == clust_label[i]]
        met_file["burst_count"][ind] = burst_count[i]
        met_file["burst_freq"][ind] = burst_count[i]/rec_len


    met_file.to_csv(metrics_file, sep='\t')


C:\Users\alexc\AppData\Local\Temp\ipykernel_78352\1863549805.py:33: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  met_file["burst_count"][ind] = burst_count[i]
C:\Users\alexc\AppData\Local\Temp\ipykernel_78352\1863549805.py:33: SettingWithCo

In [54]:
np.max(spike_times)/sample_rate

758.6455333333333

In [ ]:
met_file = pd.read_csv(r"C:\Users\alexc\Desktop\Neuron_Tracking\Mark_Sleep\M1\D1\metrics.tsv", sep='\t')
met_file["burst_count"] = np.zeros(len(met_file["cluster_id"]))

for i in range(len(clust_label)):
    ind = met_file.index[met_file["cluster_id"] == clust_label[i]]
    met_file["burst_count"][ind] = burst_count[i]

met_file.to_csv(r"C:\Users\alexc\Desktop\Neuron_Tracking\Mark_Sleep\M1\D1\metrics.tsv", sep='\t')

C:\Users\alexc\AppData\Local\Temp\ipykernel_78352\1059230551.py:7: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  met_file["burst_count"][ind] = burst_count[i]
C:\Users\alexc\AppData\Local\Temp\ipykernel_78352\1059230551.py:7: SettingWithCopy